# HW4- TfIdfVectorizer

In [1]:
import os
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report

# Read Emails

Reading Order 
1. train spam (part1-part9)
2. train ham (kitchen-l)
3. test spam (part10-part12)
4. test ham (lokay-m)

In [2]:
train_spam_folders = ["part1", "part2", "part3", "part4", "part5", "part6", "part7", "part8", "part9"]
test_spam_folders = ["part10", "part11", "part12"]

spam_dir = ".\GP"
train_spam_emails = []
train_ham_emails = []
test_spam_emails = []
test_ham_emails = []


# train spam 
for folder in train_spam_folders: 
    for root, dirs, files in os.walk(os.path.join(spam_dir, folder)):
        for name in files:
            file_path = os.path.join(root, name) 
            with open(file_path) as f:
                data = f.read()
            train_spam_emails.append(data)

# train ham 
for root, dirs, files in os.walk(os.path.join(".\kitchen-l")):
    for name in files:
        file_path = os.path.join(root, name) 
        with open(file_path, errors='surrogateescape') as f:
            data = f.read()
        train_ham_emails.append(data)

# test spam 
for folder in test_spam_folders: 
    for root, dirs, files in os.walk(os.path.join(spam_dir, folder)):
        for name in files:
            file_path = os.path.join(root, name) 
            with open(file_path) as f:
                data = f.read()
            test_spam_emails.append(data) 

# test ham 
for root, dirs, files in os.walk(os.path.join(".\lokay-m")):
    for name in files:
        file_path = os.path.join(root, name) 
        with open(file_path, errors='surrogateescape') as f:
            data = f.read()
        test_ham_emails.append(data)

In [3]:
test_spam_emails

['From: <242845@delphi.com>\nTo: <paliourg@cs.man.ac.uk>\nSubject:                 Discount code 242845\nDate: Sat, 13 Mar 2004 22:40:44 +0300\nMIME-Version: 1.0\nContent-Type: text/html;\n\tcharset="iso-8859-7"\nContent-Transfer-Encoding: quoted-printable\nX-Priority: 3\nX-MSMail-Priority: Normal\nX-MimeOLE: Produced By Microsoft MimeOLE V6.00.2900.2527\n\n<html>\n<head>\n<meta http-equiv=3D"Content-Type" content=3D"text/html; =\ncharset=3Diso-8859-1">\n<title>OEM Software</title>\n</head>\n<body bgcolor=3D"#336699">\n<div align=3D"center">\n<table border=3D"0" width=3D"600" cellspacing=3D"0" cellpadding=3D"14">\n<tr>\n<td bgcolor=3D"#FF6600" height=3D"10" valign=3D"middle" =\nalign=3D"center">\n<center><font size=3D"5"><a =\nhref=3D"http://www.valuedsoft.biz/?242845"><font =\ncolor=3D"black">Specials good thru 11/12/03. Please use discount code =\nmail9221 to receive these prices.<br><br>\nSoftware: Windows XP Suites, Adobe software, Clearance, Corel Draw/Corel =\nVentura, Games, 3D 

In [41]:
spam = train_spam_emails + test_spam_emails
ham = train_ham_emails + test_ham_emails
train = train_spam_emails + train_ham_emails
test = test_spam_emails + test_ham_emails
all_emails = train_spam_emails + train_ham_emails + test_spam_emails + test_ham_emails

# TfidfVectorizer

Top 25 words in one spam message

In [4]:
tfIdfVectorizer = TfidfVectorizer(use_idf=True)
tfIdf = tfIdfVectorizer.fit_transform(spam)
df = pd.DataFrame(tfIdf[0].T.todense(), index=tfIdfVectorizer.get_feature_names(), columns=["TF-IDF"])
df = df.sort_values('TF-IDF', ascending=False)
print (df.head(25))

                 TF-IDF
hoodia         0.433707
3d             0.398106
hoodiashop     0.254452
td             0.236018
1039           0.216853
strong         0.175282
webstat        0.169635
tr             0.149445
font           0.144737
cactus         0.143405
serif          0.136825
map            0.136344
helvetica      0.133508
sans           0.123358
width          0.113401
tablets        0.107112
diet           0.105157
arial          0.104686
face           0.101845
20             0.091411
tbody          0.091212
pict           0.084817
swisspresence  0.084817
tabs           0.084143
table          0.078602


Top 25 words in one ham message

In [5]:
tfIdfVectorizer = TfidfVectorizer(use_idf=True)
tfIdf = tfIdfVectorizer.fit_transform(ham)
df = pd.DataFrame(tfIdf[0].T.todense(), index=tfIdfVectorizer.get_feature_names(), columns=["TF-IDF"])
df = df.sort_values('TF-IDF', ascending=False)
print (df.head(25))

               TF-IDF
db           0.287360
asset        0.251269
sales        0.189747
people       0.189732
and          0.187754
team         0.179586
that         0.159656
maintained   0.157894
to           0.151978
we           0.146984
development  0.140541
in           0.137500
of           0.115195
donahue      0.107326
the          0.107209
addition     0.104427
ross         0.101706
mitch        0.100801
including    0.096133
true         0.092662
issues       0.091946
ways         0.091544
technical    0.088771
cn           0.086556
13752014     0.086127


# Random Forest Classifier

In [42]:
# true positive (spam), false positive, true negative (ham) and false negatives.

Xtrain = tfIdfVectorizer.fit_transform(all_emails)[:len(train)]
ytrain = [1] * len(train_spam_emails) + [0] * len(train_ham_emails)

Xtest = tfIdfVectorizer.fit_transform(all_emails)[len(train):]
ytest = [1] * len(test_spam_emails) + [0] * len(test_ham_emails)

print(Xtrain.shape)
print(Xtest.shape)

(14308, 413455)
(5787, 413455)


In [34]:
model = RandomForestClassifier(n_estimators=100, random_state=42)
model.fit(Xtrain, ytrain)
ypred = model.predict(Xtest)

Confusion Matrix Results 

True Positives: 3423

True Negatives: 2359 

False Positives: 5

False Negatives: 0

In [47]:
print("Confusion Matrix\n")
print(confusion_matrix(ytest, ypred)) 
print("\n-----------\n\nClassification Report: \n")
print(classification_report(ytest, ypred))

Confusion Matrix

[[2359    5]
 [   0 3423]]

-----------

Classification Report: 

              precision    recall  f1-score   support

           0       1.00      1.00      1.00      2364
           1       1.00      1.00      1.00      3423

    accuracy                           1.00      5787
   macro avg       1.00      1.00      1.00      5787
weighted avg       1.00      1.00      1.00      5787



# REDO: Use stop words in TfidfVectorizer

In [73]:
stopwords = []

with open('stopwords.txt', encoding="utf-8") as f:
    data = f.read()
    stopwords = data.split()

with open('html_tags.txt', encoding="utf-8") as f:
    data = f.read()
    stopwords += data.split()

stopwords.append('enron')

REDO: Top 25 words in one spam message using stopwords

In [77]:
tfIdfVectorizer = TfidfVectorizer(use_idf=True, stop_words=stopwords, analyzer='word')
tfIdf = tfIdfVectorizer.fit_transform(spam)
df = pd.DataFrame(tfIdf[0].T.todense(), index=tfIdfVectorizer.get_feature_names(), columns=["TF-IDF"])
df = df.sort_values('TF-IDF', ascending=False)
print (df.head(25))

C:\Users\MEI-KUEI LU\anaconda3\lib\site-packages\sklearn\feature_extraction\text.py:383: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['abbr', 'acronym', 'address', 'ain', 'applet', 'article', 'audio', 'base', 'basefont', 'bdo', 'blockquote', 'body', 'button', 'canvas', 'center', 'cite', 'code', 'col', 'colgroup', 'daren', 'datalist', 'dd', 'del', 'dfn', 'div', 'dl', 'doctype', 'dt', 'em', 'embed', 'fieldset', 'figcaption', 'figure', 'font', 'footer', 'form', 'frame', 'frameset', 'h1', 'hadn', 'head', 'header', 'herse', 'himse', 'iframe', 'img', 'input', 'ins', 'itse', 'kbd', 'label', 'legend', 'link', 'main', 'map', 'mark', 'mayn', 'meta', 'meter', 'mightn', 'mon', 'mustn', 'myse', 'nav', 'needn', 'noscript', 'object', 'ol', 'optgroup', 'option', 'oughtn', 'param', 'pre', 'progress', 'samp', 'script', 'select', 'shan', 'source', 'span', 'standard', 'strike', 'strong', 'style', 'table', 'tbody', 'textarea', 'tfoot'

                 TF-IDF
hoodia         0.467555
3d             0.429177
hoodiashop     0.274311
1039           0.233778
strong         0.188962
webstat        0.182874
font           0.156033
cactus         0.154597
serif          0.147504
map            0.146985
helvetica      0.143928
sans           0.132985
tablets        0.115472
diet           0.113364
arial          0.112856
20             0.098545
tbody          0.098331
swisspresence  0.091437
pict           0.091437
tabs           0.090710
table          0.084736
coords         0.082775
rect           0.079748
shape          0.069786
weight         0.066787


REDO: Top 25 words in one ham message using stopwords

In [78]:
tfIdfVectorizer = TfidfVectorizer(use_idf=True, stop_words=stopwords, analyzer='word')
tfIdf = tfIdfVectorizer.fit_transform(ham)
df = pd.DataFrame(tfIdf[0].T.todense(), index=tfIdfVectorizer.get_feature_names(), columns=["TF-IDF"])
df = df.sort_values('TF-IDF', ascending=False)
print (df.head(25))

C:\Users\MEI-KUEI LU\anaconda3\lib\site-packages\sklearn\feature_extraction\text.py:383: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['abbr', 'acronym', 'address', 'ain', 'applet', 'article', 'audio', 'base', 'basefont', 'bdo', 'blockquote', 'body', 'button', 'canvas', 'center', 'cite', 'code', 'col', 'colgroup', 'daren', 'datalist', 'dd', 'del', 'dfn', 'div', 'dl', 'doctype', 'dt', 'em', 'embed', 'fieldset', 'figcaption', 'figure', 'font', 'footer', 'form', 'frame', 'frameset', 'h1', 'hadn', 'head', 'header', 'herse', 'himse', 'iframe', 'img', 'input', 'ins', 'itse', 'kbd', 'label', 'legend', 'link', 'main', 'map', 'mark', 'mayn', 'meta', 'meter', 'mightn', 'mon', 'mustn', 'myse', 'nav', 'needn', 'noscript', 'object', 'ol', 'optgroup', 'option', 'oughtn', 'param', 'pre', 'progress', 'samp', 'script', 'select', 'shan', 'source', 'span', 'standard', 'strike', 'strong', 'style', 'table', 'tbody', 'textarea', 'tfoot'

                 TF-IDF
db             0.358623
asset          0.313581
sales          0.236802
people         0.236783
team           0.224122
maintained     0.197050
development    0.175394
donahue        0.133942
addition       0.130323
ross           0.126928
mitch          0.125799
including      0.119973
true           0.115641
issues         0.114748
technical      0.110785
13752014       0.107485
competent      0.107485
1075840807244  0.107485
core           0.106028
jeff           0.103877
ctg            0.099269
facilitates    0.099269
require        0.096899
incumbent      0.094462
subset         0.092635


# REDO: Random Forest Classifier using stopwords

In [80]:
# true positive (spam), false positive, true negative (ham) and false negatives.

Xtrain = tfIdfVectorizer.fit_transform(all_emails)[:len(train)]
ytrain = [1] * len(train_spam_emails) + [0] * len(train_ham_emails)

Xtest = tfIdfVectorizer.fit_transform(all_emails)[len(train):]
ytest = [1] * len(test_spam_emails) + [0] * len(test_ham_emails)

print(Xtrain.shape)
print(Xtest.shape)

(14308, 412321)
(5787, 412321)


In [81]:
model = RandomForestClassifier(n_estimators=100, random_state=42)
model.fit(Xtrain, ytrain)
ypred = model.predict(Xtest)

Confusion Matrix Results

True Positives: 3423

True Negatives: 2360

False Positives: 4

False Negatives: 0

In [82]:
print("Confusion Matrix\n")
print(confusion_matrix(ytest, ypred)) 
print("\n-----------\n\nClassification Report: \n")
print(classification_report(ytest, ypred))

Confusion Matrix

[[2360    4]
 [   0 3423]]

-----------

Classification Report: 

              precision    recall  f1-score   support

           0       1.00      1.00      1.00      2364
           1       1.00      1.00      1.00      3423

    accuracy                           1.00      5787
   macro avg       1.00      1.00      1.00      5787
weighted avg       1.00      1.00      1.00      5787



In [84]:
tfIdfVectorizer.get_stop_words()

frozenset({'sec',
           'name',
           'kr',
           'lately',
           'thatve',
           'seen',
           '<area>',
           'little',
           'vc',
           '<li>',
           'important',
           'then',
           'none',
           'open',
           'looking',
           '<fieldset>',
           'look',
           'come',
           'ru',
           'md',
           'self',
           'likely',
           'since',
           'proud',
           'hopefully',
           'whoever',
           '<dd>',
           'million',
           "here's",
           'ge',
           'younger',
           'somebody',
           'her',
           'whats',
           'va',
           'om',
           'test',
           'interested',
           'rather',
           'itll',
           'higher',
           'anyone',
           'interests',
           'sup',
           "she'd",
           'seven',
           'amount',
           'cases',
           "might've",
           'o